**This class work was made my me (Pedro Seixas) and Rita Peixoto**

In [1]:
#%matplotlib notebook
%matplotlib
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation, rc
import matplotlib
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.layers import Dense, Conv2D, Conv1D, MaxPooling2D, Dropout, Flatten

Using matplotlib backend: agg


In [2]:
#global variable for cherry
C = 1
#global array for the direction
d = np.array([[0,1], [-1,0], [0,-1], [1,0]])

In [3]:
#clear field
def clear(g):
    g *= 0
    L = len(g)
    for a in range(L):
        g[a,0] = 2
        g[a,L-1] = 2
        g[0,a] = 2
        g[L-1,a] = 2

In [4]:
#add a cherry to a random empty space
def add_cherry(g):
    zero = np.where(g==0)
    r = np.random.randint(len(zero[0]))
    g[zero[0][r]][zero[1][r]] = C

In [5]:
#add snake to the field array g=3 -> head, g=4 -> rest of the snake (only used in visualization)
def add_snake(g,snake):
    kigyo = 3
    for s in snake:
        g[s[0],s[1]] = kigyo
        kigyo = 4

In [6]:
#return what is ahead
def check_head(g, snake, ir):
    head = np.array(snake[0])
    head += d[ir]
    return g[head[0]][head[1]]

In [7]:
#mode snake, if it had eaten a cherry then make it longer
def move_snake(g, snake, ir, cherry):
    head = np.array(snake[0])
    g[head[0],head[1]] = 4
    head += d[ir]
    g[head[0],head[1]] = 3
    snake.insert(0,list(head))
    if not cherry:
        tail = snake.pop()
        g[tail[0],tail[1]] = 0

In [8]:
#generate the ionput for th NN based on the current position. it returns an array of length 8
def get_input(g,snake):
    cherry = np.where(g == C)
    c = np.array([cherry[0][0],cherry[1][0]])
    data = np.zeros(8,dtype=int)
    #first four is wether we can go in that direction
    for i in range(4):
        data[i] = check_head(g,snake,i) < 2
    #next four if the cherry is in that direction
    head = np.array(snake[0])
    for i in range(4):
        data[4 + i] = np.dot(d[i],c - head) > 0
    return(data)

In [9]:
#Makes a single step
def one_step(g,snake,nd):
    ahead = check_head(g, snake, nd)
    if ahead == C:
        return 10
    elif ahead >= 2:
        return -10
    return 0

In [10]:
#setup the game
def setup(L):
    L2 = int(L/2)
    snake = [[L2,L2],[L2,L2+1],[L2+1,L2+1]]
    g = np.zeros((L,L), dtype=int)
    clear(g)
    add_snake(g,snake)
    add_cherry(g)
    return [g, snake]

In [11]:
#This does not work in function. Can anyone tell me why???
def anim_snake(save):
    fig = plt.figure()
    ims = []
    for s in save:
        im = plt.imshow(s, animated=True)
        ims.append([im])
    ani = animation.ArtistAnimation(fig, ims, interval=50, blit=True, repeat_delay=0)
    plt.show()
    return ims

In [19]:
#Make it a little bit more comlpicated with two layers. You can modify this too
#Especially the learning rate!
model = Sequential()
model.add(Dense(units = 20, input_dim = 8, activation='relu'))
model.add(Dropout(0.15))
model.add(Dense(units = 4, activation='softmax'))
model.compile(loss='mse', optimizer=Adam(0.01))
model.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_4 (Dense)             (None, 20)                180       
                                                                 
 dropout_2 (Dropout)         (None, 20)                0         
                                                                 
 dense_5 (Dense)             (None, 4)                 84        
                                                                 
Total params: 264
Trainable params: 264
Non-trainable params: 0
_________________________________________________________________


### TASK Reinforced learning
Complete the following routine to achieve a reasonable snake (you must also tune parameters)

In [20]:
#We make the size of the screen smaller so that it can get the cherry
L = 16
#Self forgetting rate gamma
gamma = 0.9
early_random = 50
imgs = []
for game in range(150):
    [g, snake] = setup(L)
    ch = 0
    #we store the last game in last for review
    last = []
    reward = 0.0
    for i in range(500):
        #Store game in last
        last.append(np.copy(g))
        #predict our next move
        predict = model.predict(get_input(g, snake).reshape(1,8), verbose = 0)
        #in the early stage randomize moviements for exploration
        if game < early_random and np.random.random() < (early_random - game) / early_random / 2:
            nd = np.random.randint(4)
        else:
            nd = predict.argmax()
        #Check what is ahead
        ahead = one_step(g, snake, nd)
        #TASK: Make a reward calculation possibilities number of steps made
        #(positive feedback at the beginning but negative at late stage), sum of cheries
        state_reward = 20 - i * 0.1
        if ahead > 0: state_reward += 250 # Cherry
        if ahead < 0: state_reward -= 1000 # Wall or snake
        #Change the target value for the direction nd(keep gamma part and add reward),
        #  for other directions we keep the predicted values of predict
        target = predict
        target[0][nd] = gamma * predict[0][nd] + state_reward
        reward += state_reward
        #teach a model for one epoch with the new target
        model.fit(get_input(g, snake).reshape(1,8), target, epochs = 1, verbose = 0)
        #If we have eaten the cherry add a new one or 
        #if we have hit something, then exit the game
        if ahead > 0:
            add_cherry(g)
            ch += 1
        if ahead < 0:
            break
        #Huhh, we survived, so move on
        move_snake(g, snake, nd, ahead > 0)
    #Print where we are
    print(game,i,ch,reward)
    imgs.append(last)
#IMPORTANT: If you rerun this, it starts from the old weights, if you rerun the model creation first than
#  it starts from random weights.

0 1 0 -960.1
1 0 0 -980.0
2 3 0 -920.5999999999999
3 1 0 -960.1
4 1 0 -960.1
5 2 0 -940.3000000000001
6 4 0 -901.0
7 14 0 -710.5
8 0 0 -980.0
9 3 0 -920.5999999999999
10 5 0 -881.5
11 0 0 -980.0
12 4 0 -901.0
13 18 0 -637.0999999999999
14 7 0 -842.8000000000001
15 2 0 -940.3000000000001
16 1 0 -960.1
17 7 0 -842.8000000000001
18 8 0 -823.5999999999999
19 13 0 -729.0999999999999
20 6 0 -862.1
21 7 0 -842.8000000000001
22 5 0 -881.5
23 13 1 -479.0999999999999
24 6 0 -862.1
25 10 0 -785.5
26 10 0 -785.5
27 4 0 -901.0
28 9 0 -804.5
29 1 0 -960.1
30 11 0 -766.6
31 6 0 -862.1
32 10 0 -785.5
33 21 0 -583.0999999999999
34 7 0 -842.8000000000001
35 25 1 -262.5
36 20 0 -601.0
37 1 0 -960.1
38 3 0 -920.5999999999999
39 19 0 -619.0
40 5 0 -881.5
41 26 0 -495.09999999999997
42 39 0 -277.9999999999999
43 23 0 -547.5999999999999
44 18 0 -637.0999999999999
45 8 0 -823.5999999999999
46 39 0 -277.9999999999999
47 59 0 23.000000000000114
48 43 0 -214.5999999999999
49 97 0 484.70000000000005
50 146 0 866.

In [21]:
#Just check the length of the last game, I do not lake to play 500 images...
len(last)

500

In [22]:
#review last at last
fig = plt.figure()
ims = []
for s in last:
    im = plt.imshow(s, animated=True)
    ims.append([im])
ani = animation.ArtistAnimation(fig, ims, interval=50, blit=True, repeat_delay=0)
plt.show()

In [23]:
rc('animation', html='jshtml')
ani